In [12]:
%pip list


Package                      Version
---------------------------- --------
absl-py                      1.4.0
asttokens                    2.2.1
attrs                        22.2.0
autopep8                     2.0.2
backcall                     0.2.0
colorama                     0.4.6
comm                         0.1.2
comtypes                     1.1.14
contourpy                    1.0.7
cycler                       0.11.0
debugpy                      1.6.6
decorator                    5.1.1
executing                    1.2.0
flatbuffers                  23.3.3
fonttools                    4.39.0
ipykernel                    6.21.3
ipython                      8.11.0
jedi                         0.18.2
jupyter_client               8.0.3
jupyter_core                 5.2.0
kiwisolver                   1.4.4
libclang                     16.0.0
matplotlib                   3.7.1
matplotlib-inline            0.1.6
mediapipe                    0.9.1.0
nest-asyncio                 1.5.6
nump


[notice] A new release of pip is available: 23.0.1 -> 23.1.2
[notice] To update, run: python.exe -m pip install --upgrade pip


In [13]:
%pip install tensorflow


  Using cached tensorflow-2.12.0-cp310-cp310-win_amd64.whl (1.9 kB)
  Using cached tensorflow_intel-2.12.0-cp310-cp310-win_amd64.whl (272.8 MB)
  Using cached grpcio-1.54.2-cp310-cp310-win_amd64.whl (4.1 MB)
  Using cached tensorboard-2.12.3-py3-none-any.whl (5.6 MB)
  Using cached jax-0.4.11-py3-none-any.whl
  Using cached gast-0.4.0-py3-none-any.whl (9.8 kB)
  Using cached h5py-3.8.0-cp310-cp310-win_amd64.whl (2.6 MB)
  Using cached google_pasta-0.2.0-py3-none-any.whl (57 kB)
  Using cached astunparse-1.6.3-py2.py3-none-any.whl (12 kB)
  Using cached keras-2.12.0-py2.py3-none-any.whl (1.7 MB)
  Using cached opt_einsum-3.3.0-py3-none-any.whl (65 kB)
  Using cached scipy-1.10.1-cp310-cp310-win_amd64.whl (42.5 MB)
  Using cached ml_dtypes-0.2.0-cp310-cp310-win_amd64.whl (938 kB)
  Using cached Werkzeug-2.3.5-py3-none-any.whl (242 kB)
  Using cached google_auth_oauthlib-1.0.0-py2.py3-none-any.whl (18 kB)
  Using cached google_auth-2.19.1-py2.py3-none-any.whl (181 kB)
  Using cached requ


[notice] A new release of pip is available: 23.0.1 -> 23.1.2
[notice] To update, run: python.exe -m pip install --upgrade pip


In [1]:
import cv2
import os
import random
import numpy as np
from matplotlib import pyplot as plt

In [2]:
import tensorflow as tf
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Layer,Conv2D,Dense,MaxPooling2D, Input, Flatten


In [3]:
# Avoid OOM errors by setting GPU Memory Consumption Growth
gpus = tf.config.experimental.list_physical_devices('GPU')
for gpu in gpus:
    tf.config.experimental.set_memory_growth(gpu, True)

In [4]:

# Setup paths
POS_PATH = os.path.join('data', 'positive')
NEG_PATH = os.path.join('data', 'negative')
ANC_PATH = os.path.join('data', 'anchor')

In [5]:

# Make the directories
os.makedirs(POS_PATH)
os.makedirs(NEG_PATH)
os.makedirs(ANC_PATH)

In [9]:
# http://vis-www.cs.umass.edu/lfw/
# Uncompress Tar GZ Labelled Faces in the Wild Dataset
!tar -xf lfw.tgz

In [10]:
# Move LFW Images to the following repository data/negative
for directory in os.listdir('lfw'):
    for file in os.listdir(os.path.join('lfw', directory)):
        EX_PATH = os.path.join('lfw', directory, file)
        NEW_PATH = os.path.join(NEG_PATH, file)
        os.replace(EX_PATH, NEW_PATH)


# Collecting Data

In [5]:
import uuid

In [6]:
num_anchors=3000
num_pos=3000

In [30]:
cam=cv2.VideoCapture(0)

captured=0

#Capturing anchors in user friendly way
while True:
    check, frame = cam.read()

    if (cv2.waitKey(1) & 0XFF) == ord('q'):
        break

    if(check and captured<num_anchors):

        cv2.imshow('Image Collection', frame)
        frame = frame[120:120+250, 200:200+250]
        path = os.path.join(ANC_PATH, str(uuid.uuid1())+'.jpg')
        cv2.imwrite(path, frame)
        captured+=1
    

cam.release()
cv2.destroyAllWindows()


In [31]:
cam = cv2.VideoCapture(0)

captured = 0

# Capturing positives in user friendly way only issue is that the frame freezes aftetr taking 300 pics
while True:
    check, frame = cam.read()

    if (cv2.waitKey(1) & 0XFF) == ord('q'):
        break

    if (check and captured < num_anchors): #we can give a pop up once this is done.

        cv2.imshow('Image Collection', frame)
        frame = frame[120:120+250, 200:200+250]
        path = os.path.join(POS_PATH, str(uuid.uuid1())+'.jpg')
        cv2.imwrite(path, frame)
        captured += 1


cam.release()
cv2.destroyAllWindows()


In [18]:
# cam=cv2.VideoCapture(0)

# while True:
#     check,frame=cam.read()

#     cv2.imshow('Image Collection', frame)

#     frame=frame[120:120+250,200:200+250]   
    
#     #need to add gridlines in image frame so that people only keep their face in this region of their frame

#     if (cv2.waitKey(1) & 0XFF) == ord('q'):
#         break

#     if (cv2.waitKey(1) & 0XFF) == ord('a'):  
#         #have to find a way to modify this and make it more user friendly, instead of making user capture 300 images.

#         path = os.path.join(ANC_PATH, str(uuid.uuid1())+'.jpg')
#         cv2.imwrite(path, frame)

#     if (cv2.waitKey(1) & 0XFF) == ord('p'):
#         # have to find a way to modify this and make it more user friendly, instead of making user capture 300 images.

#         path = os.path.join(POS_PATH, str(uuid.uuid1())+'.jpg')
#         cv2.imwrite(path, frame)

# cam.release()
# cv2.destroyAllWindows()

# Creating Labelled Dataset

In [7]:
def preprocess(file_path):

    byte_img = tf.io.read_file(file_path)
    # Load in the image
    img = tf.io.decode_jpeg(byte_img)

    img = tf.image.resize(img, (105, 105))
    # Scale image to be between 0 and 1
    img = img / 255.0
    return img


In [8]:


def preprocess_twin(input_img, validation_img, label):
    return (preprocess(input_img), preprocess(validation_img), label)


In [20]:
# We can try data augmentation to increase accuracy but it will increase the training time. 


# #Doing Data Augmentation

# def data_aug(img):
#     data = []
#     for i in range(9):
#         img = tf.image.stateless_random_brightness(img, max_delta=0.02, seed=(1,2))
#         img = tf.image.stateless_random_contrast(img, lower=0.6, upper=1, seed=(1,3))
#         # img = tf.image.stateless_random_crop(img, size=(20,20,3), seed=(1,2))
#         img = tf.image.stateless_random_flip_left_right(img, seed=(np.random.randint(100),np.random.randint(100)))
#         img = tf.image.stateless_random_jpeg_quality(img, min_jpeg_quality=90, max_jpeg_quality=100, seed=(np.random.randint(100),np.random.randint(100)))
#         img = tf.image.stateless_random_saturation(img, lower=0.9,upper=1, seed=(np.random.randint(100),np.random.randint(100)))
            
#         data.append(img)
    
#     return data


# for file in os.listdir(POS_PATH):
#     file_path = os.path.join(POS_PATH, file)
#     img=cv2.imread(file_path)
    
#     img_aug_list=data_aug(img)

#     for i in img_aug_list:
#         cv2.imwrite(os.path.join(POS_PATH, str(uuid.uuid1())+'.jpg'), i.numpy())
    

# for file in os.listdir(ANC_PATH):
#     file_path = os.path.join(ANC_PATH, file)
#     img = cv2.imread(file_path)

#     img_aug_list = data_aug(img)

#     for i in img_aug_list:
#         cv2.imwrite(os.path.join(ANC_PATH, str(uuid.uuid1())+'.jpg'), i.numpy())


In [9]:
import glob


In [10]:
anchor = tf.data.Dataset.from_tensor_slices(glob.glob(ANC_PATH+'\*.jpg')).take(3000)
positive = tf.data.Dataset.from_tensor_slices(glob.glob(POS_PATH+'\*.jpg')).take(3000)
negative = tf.data.Dataset.from_tensor_slices(glob.glob(NEG_PATH+'\*.jpg')).take(3000)

# Converting all the data into tensorflow dataset

In [11]:
img=preprocess("data\\anchor\\74748cba-0900-11ee-8163-f889d2136612.jpg")

In [12]:
img.numpy().shape

(105, 105, 3)

In [13]:
dataset_pos=tf.data.Dataset.zip((anchor,positive,tf.data.Dataset.from_tensor_slices(tf.ones(len(anchor)))))
dataset_neg=tf.data.Dataset.zip((anchor,negative,tf.data.Dataset.from_tensor_slices(tf.zeros(len(anchor)))))

# y_dataset_pos=tf.data.Dataset.from_tensor_slices(tf.ones(len(anchor)))
# y_dataset_neg=tf.data.Dataset.from_tensor_slices(tf.zeros(len(anchor)))

# y_dataset=y_dataset_pos.concatenate(y_dataset_neg)

In [14]:
dataset=dataset_pos.concatenate(dataset_neg)
dataset = dataset.map(preprocess_twin)
# seed=42

dataset=dataset.shuffle(buffer_size=len(anchor))  #setting the seeds so that the y_dataset and training data is shuffled in same order.

# y_dataset = y_dataset.shuffle(buffer_size=len(anchor), seed=seed)




In [58]:
for data in dataset:
    print(data)

#testing out the dataset formation 

(<tf.Tensor: shape=(105, 105, 3), dtype=float32, numpy=
array([[[0.1322151 , 0.096921  , 0.07731315],
        [0.13259304, 0.10514206, 0.08161265],
        [0.1375239 , 0.10829888, 0.09009159],
        ...,
        [0.7568516 , 0.76469475, 0.7215575 ],
        [0.7569494 , 0.76479256, 0.7216553 ],
        [0.75686276, 0.7647059 , 0.7137255 ]],

       [[0.14145659, 0.10588235, 0.08711484],
        [0.1459584 , 0.11766706, 0.0952581 ],
        [0.14618514, 0.1162465 , 0.09877951],
        ...,
        [0.749173  , 0.7570161 , 0.71387887],
        [0.7529412 , 0.7607843 , 0.7176471 ],
        [0.75686276, 0.7647059 , 0.72156864]],

       [[0.14265928, 0.10344359, 0.09560046],
        [0.14979991, 0.11058423, 0.10274109],
        [0.15626472, 0.11785159, 0.10760082],
        ...,
        [0.75783426, 0.7664799 , 0.72334266],
        [0.7607843 , 0.7669801 , 0.72878486],
        [0.7586368 , 0.7647059 , 0.7268908 ]],

       ...,

       [[0.09722112, 0.16751815, 0.19751239],
        [0.1

KeyboardInterrupt: 

In [29]:
while True:

    image1 = cv2.imread("data\\anchor\\969eac7a-0900-11ee-8a48-f889d2136612.jpg")
    cv2.imshow("Input",image1)

    image2 = cv2.imread("data\\negative\\Danis_Tanovic_0001.jpg")
    cv2.imshow("Validation",image2)

    if (cv2.waitKey(1) & 0XFF) == ord('q'):
        break

cv2.destroyAllWindows()


In [26]:
dataset_train=dataset.take(int(0.7*len(dataset)))
dataset_train=dataset_train.batch(16).repeat(16)
dataset_train = dataset_train.prefetch(8)


dataset_test=dataset.skip(int(0.7*len(dataset)))
# y_dataset_test = y_dataset.skip(int(0.7*len(dataset)))

print(len(dataset_test))
print(len(dataset_train))
print(len(dataset))


1800
4208
6000


In [17]:
# print(len(y_dataset_test))
# print(len(y_dataset_train))
# print(len(y_dataset))


# Making the Neural Network and Training the Data

In [18]:
def initial_layers():

    inp=Input(shape=(105,105,3),name="Input_layer")

    conv1=Conv2D(64,(10,10),activation='relu',name="ConvOfBlock1")(inp)
    mp1=MaxPooling2D(64,(2,2),padding='same')(conv1)

    conv2 = Conv2D(128, (7, 7), activation='relu', name="ConvOfBlock2")(mp1)
    mp2=MaxPooling2D(64,(2,2),padding='same')(conv2)

    conv3 = Conv2D(128, (4, 4), activation='relu', name="ConvOfBlock3")(mp2)
    mp3 = MaxPooling2D(64, (2, 2), padding='same')(conv3)

    conv4 = Conv2D(256, (4, 4), activation='relu', name="ConvOfBlock4")(mp3)

    f1 = Flatten()(conv4)
    d1 = Dense(4096, activation='sigmoid')(f1)


    return Model(inputs=[inp],outputs=[d1],name="embedding")


In [19]:
basic_layer=initial_layers()

In [20]:
basic_layer.summary()

Model: "embedding"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 Input_layer (InputLayer)    [(None, 105, 105, 3)]     0         
                                                                 
 ConvOfBlock1 (Conv2D)       (None, 96, 96, 64)        19264     
                                                                 
 max_pooling2d (MaxPooling2D  (None, 48, 48, 64)       0         
 )                                                               
                                                                 
 ConvOfBlock2 (Conv2D)       (None, 42, 42, 128)       401536    
                                                                 
 max_pooling2d_1 (MaxPooling  (None, 21, 21, 128)      0         
 2D)                                                             
                                                                 
 ConvOfBlock3 (Conv2D)       (None, 18, 18, 128)       26

In [21]:
class siamese(Layer):
   
   def __init__(self, **kwargs):
        super().__init__()
   
   def call(self,inp_model_processed,validation_model_processed):
      return tf.math.abs(inp_model_processed-validation_model_processed)

In [22]:
def model():
    inp_image=Input(shape=(105,105,3),name="Input/AnchorImg")
    valid_image=Input(shape=(105,105,3),name="ValidationImg")

    inp_data=basic_layer(inp_image)
    valid_data=basic_layer(valid_image)

    L1layer=siamese()

    distance = L1layer(inp_data, valid_data)

    last_layer=Dense(1,activation='sigmoid')(distance)

    return Model(inputs=[inp_image,valid_image],outputs=[last_layer],name="SiamesesNeuralNetwork")

In [23]:
snn=model()

In [24]:
snn.summary()

Model: "SiamesesNeuralNetwork"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 Input/AnchorImg (InputLayer)   [(None, 105, 105, 3  0           []                               
                                )]                                                                
                                                                                                  
 ValidationImg (InputLayer)     [(None, 105, 105, 3  0           []                               
                                )]                                                                
                                                                                                  
 embedding (Functional)         (None, 4096)         38960448    ['Input/AnchorImg[0][0]',        
                                                                  'ValidationI

In [27]:

snn.compile(
    loss=tf.keras.losses.BinaryCrossentropy(),
    optimizer=tf.keras.optimizers.Adam(learning_rate=0.001),
)

X_inp,X_val, labels = tf.compat.v1.data.make_one_shot_iterator(dataset_train.batch(len(dataset_train))).get_next()

snn.fit(
    [X_inp,X_val],labels,
    epochs=3
)
